In [2]:
!git clone https://github.com/raphi-web/Advanced-Topics-2.git

Klone nach 'Advanced-Topics-2' …
remote: Enumerating objects: 5, done.
remote: Counting objects: 100% (5/5), done.
remote: Compressing objects: 100% (4/4), done.
remote: Total 5 (delta 0), reused 5 (delta 0), pack-reused 0
Empfange Objekte: 100% (5/5), 1.41 MiB | 931.00 KiB/s, fertig.


In [3]:
!pip3 install -q fastai 
!pip3 install -q torchvision
!pip3 install -q geopandas
!pip3 install -q xyzservices

In [1]:
from fastai.tabular.all import *
import torch

import pandas as pd
import geopandas as gpd
import seaborn as sns
import matplotlib.pyplot as plt
import matplotlib.cm as cm
import bokeh
from bokeh.plotting import figure, show
from sklearn.model_selection import train_test_split
from sklearn.ensemble import RandomForestRegressor
from sklearn.model_selection import GridSearchCV

from bokeh.plotting import figure, output_file, show
from bokeh.tile_providers import CARTODBPOSITRON, get_provider
from bokeh.tile_providers import get_provider, Vendors
import xyzservices.providers as xyz
from bokeh.plotting import figure, show
from bokeh.models import LinearColorMapper, ColorBar, BasicTicker

In [2]:
bokeh.io.output_notebook()

Loading BokehJS ...

In [3]:
ds_path = '/content/Advanced-Topics-2/Data/housing.csv'
ds_path ="Advanced-Topics-2/Data/housing.csv"

In [4]:
df = pd.read_csv(ds_path)

In [5]:
df.head()

longitude  latitude  housing_median_age  total_rooms  total_bedrooms  \
0    -122.23     37.88                41.0        880.0           129.0   
1    -122.22     37.86                21.0       7099.0          1106.0   
2    -122.24     37.85                52.0       1467.0           190.0   
3    -122.25     37.85                52.0       1274.0           235.0   
4    -122.25     37.85                52.0       1627.0           280.0   

   population  households  median_income  median_house_value ocean_proximity  
0       322.0       126.0         8.3252            452600.0        NEAR BAY  
1      2401.0      1138.0         8.3014            358500.0        NEAR BAY  
2       496.0       177.0         7.2574            352100.0        NEAR BAY  
3       558.0       219.0         5.6431            341300.0        NEAR BAY  
4       565.0       259.0         3.8462            342200.0        NEAR BAY

In [6]:
df.describe()

longitude      latitude  housing_median_age   total_rooms  \
count  20640.000000  20640.000000        20640.000000  20640.000000   
mean    -119.569704     35.631861           28.639486   2635.763081   
std        2.003532      2.135952           12.585558   2181.615252   
min     -124.350000     32.540000            1.000000      2.000000   
25%     -121.800000     33.930000           18.000000   1447.750000   
50%     -118.490000     34.260000           29.000000   2127.000000   
75%     -118.010000     37.710000           37.000000   3148.000000   
max     -114.310000     41.950000           52.000000  39320.000000   

       total_bedrooms    population    households  median_income  \
count    20433.000000  20640.000000  20640.000000   20640.000000   
mean       537.870553   1425.476744    499.539680       3.870671   
std        421.385070   1132.462122    382.329753       1.899822   
min          1.000000      3.000000      1.000000       0.499900   
25%        296.000000    787.000000    280.000000       2.563400   
50%        435.000000   1166.000000    409.000000       3.534800   
75%        647.000000   1725.000000    605.000000       4.743250   
max       6445.000000  35682.000000   6082.000000      15.000100   

       median_house_value  
count        20640.000000  
mean        206855.816909  
std         115395.615874  
min          14999.000000  
25%         119600.000000  
50%         179700.000000  
75%         264725.000000  
max         500001.000000

In [7]:
for c in df.columns:
    print(c,"Contains NaN?:",df[c].isnull().values.any())

longitude Contains NaN?: False
latitude Contains NaN?: False
housing_median_age Contains NaN?: False
total_rooms Contains NaN?: False
total_bedrooms Contains NaN?: True
population Contains NaN?: False
households Contains NaN?: False
median_income Contains NaN?: False
median_house_value Contains NaN?: False
ocean_proximity Contains NaN?: False


In [8]:
X = "longitude" #@param ["longitude","latitude","housing_median_age","total_rooms","total_bedrooms","population","households","median_income","median_house_value","ocean_proximity"]

p = figure(width=670, height=400, toolbar_location=None,
           title="Histogram of Housing-Variables")

hist, edges = np.histogram(df[X], density=True, bins=50)
p.quad(top=hist, bottom=0, left=edges[:-1], right=edges[1:],
         fill_color="skyblue", line_color="white",
         legend_label=X)

show(p)

In [9]:
# range bounds supplied in web mercator coordinates
def lon_to_web_mercator(lon):
    k = 6378137
    return lon * (k * np.pi / 180.0)
def lat_to_web_mercator(lat):
    k = 6378137
    return np.log(np.tan((90 + lat) * np.pi / 360.0)) * k


X = "housing_median_age" #@param ["housing_median_age","total_rooms","total_bedrooms","population","households","median_income","median_house_value","ocean_proximity"]

df_vis = df.copy().drop("ocean_proximity",axis=1)

df_vis["x"] = lon_to_web_mercator(df.longitude)
df_vis["y"] = lat_to_web_mercator(df.latitude)

xmin = df_vis["x"].min()
xmax = df_vis["x"].max()
ymin = df_vis["y"].min()
ymax = df_vis["y"].max()

p = figure(
    title=f"Map of {X}",
    x_range=(xmin, xmax),
    y_range=(ymin, ymax),
    width=800,
    height=600)



minima = df_vis[X].min()
maxima = df_vis[X].max()

color_mapper = LinearColorMapper(palette="Plasma256", low=minima, high=maxima)
color_bar = ColorBar(color_mapper=color_mapper, ticker=BasicTicker(),
                     label_standoff=12, border_line_color=None, title = X)

p.add_layout(color_bar,"right")
p.scatter(
    x="x",
    y="y",
    source=df_vis,
    line_color=None,
    color={'field': X, 'transform': color_mapper},
    fill_alpha=0.3)

p.add_tile(get_provider(Vendors.CARTODBPOSITRON))



show(p)

In [10]:
#@title String fields

X = "population" #@param ["longitude","latitude","housing_median_age","total_rooms","total_bedrooms","population","households","median_income","median_house_value","ocean_proximity"]
Y = "households" #@param ["longitude","latitude","housing_median_age","total_rooms","total_bedrooms","population","households","median_income","median_house_value","ocean_proximity"]
minima = min(df.median_house_value)
maxima = max(df.median_house_value)

p = figure(width=800, height=500)
color_mapper = LinearColorMapper(palette="Plasma256", low=minima, high=maxima)
color_bar = ColorBar(color_mapper=color_mapper, ticker=BasicTicker(),
                     label_standoff=12, border_line_color=None, title = 'Housing Prices')

p.add_layout(color_bar,"right")
p.scatter(
    x=X,
    y=Y,
    color={'field': 'median_house_value', 'transform': color_mapper},
    source=df,
    fill_alpha=0.3)

p.add_tile(get_provider(Vendors.CARTODBPOSITRON))
show(p)


# Preprocessing using FastAI

In [11]:
df_test = df.sample(int(len(df) * 0.2),random_state=42)
df_train = df.drop(df_test.index)

df_test.to_csv("test.csv")
df_train.to_csv("train.csv")

In [12]:
splits = RandomSplitter(valid_pct=0.2)(range_of(df_train))

### TabularPandas completely takes care of Normalization, NAN-Filling and HotEncoding the Oceon-Proximity column

In [13]:
to = TabularPandas(df_train, procs=[Categorify, FillMissing,Normalize],
                   cat_names = ['ocean_proximity'],
                   cont_names = ['longitude', 'latitude', 'housing_median_age', 'total_rooms','total_bedrooms','population',"households","median_income"],
                   y_names='median_house_value',
                   splits=splits)

## Prepare the Dataloader

In [14]:
dls = to.dataloaders(bs=1024)

In [15]:
dls.show_batch()

# Training

In [70]:
import os
from pathlib import Path
try:
  os.mkdir("training")
except FileExistsError:
  pass


In [71]:
print(torch.cuda.device_count())
print(torch.cuda.current_device())
print(torch.cuda.is_available())
print( torch.cuda.get_device_name(0))

1
0
True
NVIDIA GeForce RTX 3060


In [74]:
learn = tabular_learner(dls,metrics=rmse)
learn.path = Path("training")

In [75]:
with learn.no_logging():
    learn.fit_one_cycle(
        10000,
        cbs=[
            EarlyStoppingCallback(monitor='valid_loss', min_delta=0.01, patience=200),
            SaveModelCallback(fname='model',monitor="valid_loss", min_delta=0.1),
            CSVLogger()
        ])


Better model found at epoch 0 with valid_loss value: 57378418688.0.
Better model found at epoch 1 with valid_loss value: 57378402304.0.
Better model found at epoch 2 with valid_loss value: 57378316288.0.
Better model found at epoch 3 with valid_loss value: 57378222080.0.
Better model found at epoch 4 with valid_loss value: 57378156544.0.
Better model found at epoch 5 with valid_loss value: 57378103296.0.
Better model found at epoch 6 with valid_loss value: 57378058240.0.
Better model found at epoch 7 with valid_loss value: 57378013184.0.
Better model found at epoch 8 with valid_loss value: 57377968128.0.
Better model found at epoch 9 with valid_loss value: 57377923072.0.
Better model found at epoch 10 with valid_loss value: 57377873920.0.
Better model found at epoch 11 with valid_loss value: 57377828864.0.
Better model found at epoch 12 with valid_loss value: 57377804288.0.
Better model found at epoch 13 with valid_loss value: 57377763328.0.
Better model found at epoch 14 with valid_lo

In [78]:
train_log_df = pd.read_csv("training/history.csv")

In [82]:
#epoch,train_loss,valid_loss,_rmse,time

Y_train = "train_loss"
Y_valid = "valid_loss"
p = figure(title="Training Metrics",
width=900, 
height=700,
x_axis_label='epoch',
y_axis_label=Y)

p.line("epoch", Y_train, legend_label=Y_train, line_width=2, source=train_log_df)
p.line("epoch", Y_valid, legend_label=Y_valid, line_width=2, source=train_log_df)
show(p)